# Dataviz with folium

Let's try using folium and geojson to generate visuals.

## Import a few modules

In [2]:
import sys
import numpy as np
import pandas as pd
import gpxpy
import matplotlib.pyplot as plt
import geopy.distance
import glob
import os
import time
from selenium import webdriver
import importlib
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
import folium
import geojson
import xyzservices.providers as xyz
from datetime import datetime

pd.options.mode.copy_on_write = True

sys.path.append("../my_modules")
import toolToReadGPX as ttrgpx

run_club_name = "RunRite"

# Load Data

In [5]:
importlib.reload(ttrgpx)

# list of file names
path_csv_files = "../data/csv/"
list_csv_files  = glob.glob(path_csv_files+run_club_name+"*_downSample.csv")
list_csv_files.sort()

# list of panda DataFrame
list_run_df = [pd.read_csv(x) for x in list_csv_files]

# DataFrame with information about all gps traces
all_last_traces_info_df = ttrgpx.fun_create_df_from_list_df(list_run_df, list_csv_files, ttrgpx.startingPoint_df, club_name = run_club_name)

# do a last cleaning to remove errands before the start of the run
list_run_df, all_last_traces_info_df  = ttrgpx.fun_traces_before_race_from_lits_df(list_run_df,
                                                                                   all_last_traces_info_df,
                                                                                   ttrgpx.startingPoint_df, debug = False)

In [14]:
!ls ../data/csv/

RunRite_2017_09_14_downSample.csv RunRite_2021_07_08_downSample.csv
RunRite_2017_09_21_downSample.csv RunRite_2021_07_15_downSample.csv
RunRite_2017_09_28_downSample.csv RunRite_2021_07_22_downSample.csv
RunRite_2017_10_05_downSample.csv RunRite_2021_07_29_downSample.csv
RunRite_2017_10_12_downSample.csv RunRite_2021_08_05_downSample.csv
RunRite_2017_10_19_downSample.csv RunRite_2021_08_12_downSample.csv
RunRite_2017_10_26_downSample.csv RunRite_2021_08_26_downSample.csv
RunRite_2017_11_02_downSample.csv RunRite_2021_09_01_downSample.csv
RunRite_2017_11_09_downSample.csv RunRite_2021_09_09_downSample.csv
RunRite_2017_11_16_downSample.csv RunRite_2021_09_16_downSample.csv
RunRite_2017_11_23_downSample.csv RunRite_2021_09_23_downSample.csv
RunRite_2017_11_30_downSample.csv RunRite_2021_09_30_downSample.csv
RunRite_2017_12_14_downSample.csv RunRite_2021_10_07_downSample.csv
RunRite_2017_12_21_downSample.csv RunRite_2021_10_14_downSample.csv
RunRite_2018_01_04_downSample.csv RunRite_2021_1

# Creating a Map

In [6]:
# Create map
westmount = folium.Map(tiles = xyz.CartoDB.DarkMatter , # CartoDB.Positron ,  # "CartoDB positron", 
                       attr  = "My Attribution",       #
                       #width=1280,height=720,
                       location = (45.4857, -73.5957), # position for Westmount
                       zoom_start = 14)

# add run traced
maxElevation = 233 # Montreal highest point
locations = []
for c in range(7):
    select_run_df = all_last_traces_info_df[(all_last_traces_info_df.index >= ttrgpx.list_starting_date[c]) &
                                            (all_last_traces_info_df.index < ttrgpx.list_starting_date[c+1])].copy()
    list_index_sel = np.array(select_run_df["indexNum"].tolist())

    # apply color per trace
    for tt in list_index_sel:
        one_run_trace  = [(x,y) for (x,y) in zip(list_run_df[tt]["latitude"].iloc[:].to_list(), 
                                                 list_run_df[tt]["longitude"].iloc[:].to_list())]
    
        one_run_elevation = [z / maxElevation for z in list_run_df[tt]["elevation"].iloc[:].to_list()] 
        
        #folium.PolyLine(one_run_trace, tooltip="one_run", color="pink").add_to(westmount)
        colors = np.ones(len(one_run_elevation))
        folium.ColorLine(positions = one_run_trace, 
                                 #tooltip = "one_run", 
                                 colors = one_run_elevation,
                                 colormap = ["pink","red"],
                                 weight=1).add_to(westmount)
        locations.extend(one_run_trace)

#HeatMap(locations,radius=10).add_to(westmount)

# Display one gpd 
westmount.save("../tmp/mapRRAC.html")
westmount

In [27]:
len(locations)

51569

# Export map as single image

# Side project around the races I took part

## Do single map for single gpx trace

But also:
+ load gpx
+ downsample gpx files
+ save as csv
+ create list of dataframe

In [12]:
importlib.reload(ttrgpx)

path_gpx_myOwnData = "../data/myRaceArchive/gpx/"
path_csv_myOwnData = "../data/myRaceArchive/csv/"

ll = glob.glob(path_gpx_myOwnData+"*.gpx")
ll.sort()
print("There is {0:1.0f} files to process.".format(len(ll)))

list_all_files_as_df = [ttrgpx.fun_gpx2pd(single_gpx) for single_gpx in ll]

# reduce the size
list_all_files_ReSample_as_df = [ttrgpx.fun_DownSample_gpx(x, number_of_sample = 400) for x in list_all_files_as_df]

# check one gpx path
list_all_files_ReSample_as_df[0].describe()

# get list of gpx file and create list of csv file name
list_gpx_file = glob.glob(path_gpx_myOwnData+"*.gpx")
list_gpx_file.sort()
list_csv_file_name = [path_csv_myOwnData+os.path.split(x)[1][0:-4]+"_downSample.csv" for x in list_gpx_file]

# export DataFrame as csv file
for c,df_ in enumerate(list_all_files_ReSample_as_df):
    df_.to_csv(list_csv_file_name[c], index=False)

There is 17 files to process.


Vilnius


In [13]:
# Create map
allRunMaps = folium.Map(tiles = xyz.CartoDB.DarkMatter, # CartoDB.Positron ,  # "CartoDB positron", 
                       attr  = "My Attribution",       #
                       #width=1280,height=720,
                       location = (45.5019, -73.5674), # position Montreal
                       zoom_start = 13)

list_run_df = list_all_files_ReSample_as_df

# add run traced
maxElevation = 114 # Berlin highest point Muggelberg
locations = []
list_index_sel = np.arange(len(list_all_files_ReSample_as_df))

# apply color per trace
for tt in list_index_sel:
    one_run_trace  = [(x,y) for (x,y) in zip(list_run_df[tt]["latitude"].iloc[:].to_list(), 
                                             list_run_df[tt]["longitude"].iloc[:].to_list())]

    one_run_elevation = [z / maxElevation for z in list_run_df[tt]["elevation"].iloc[:].to_list()] 
    
    #folium.PolyLine(one_run_trace, tooltip="one_run", color="pink").add_to(westmount)
    colors = np.ones(len(one_run_elevation))
    folium.ColorLine(positions = one_run_trace, 
                             #tooltip = "one_run", 
                             colors = one_run_elevation,
                             colormap = ["pink","red"],
                             weight=1).add_to(allRunMaps)
    locations.extend(one_run_trace)
# Display one gpd 
allRunMaps.save("../tmp/allRunMaps.html")
allRunMaps

In [22]:
mapName = "mapMontreal"
# Create map
mapSingleRace = folium.Map(tiles = xyz.CartoDB.DarkMatter, # CartoDB.Positron ,  # "CartoDB positron", 
                       attr  = "My Attribution",       #
                       #width=1280, height=720,
                       #location = (52.3650, 13.5010), # position for Berlin BER
                       #location = (52.350,13.517), # position vilalge under Vilnius
                       #location = (51.61858, 12.34017), # Bitterfeld
                       #location = (52.34357, 4.85462), # Amsterdam
                       #location  = (37.8277,-122.49939) , # Marin Headlands park
                       #location  = (45.42835,-73.67644) , # Park Rene Levesque
                       #location  = (46.80774,-71.20704) , # Quebec city
                       location  = (45.52389,-73.57171) , # Montreal Plateau
                       #location  = (45.42452, -75.69836), # Ottawa
                       #location  = (47.77238,-70.11176),# La Malbaie
                       zoom_start = 11)

list_run_df = list_all_files_ReSample_as_df

# add run traced
maxElevation = 300 # 
locations = []
list_index_sel = np.array([8,10, 12, 13, 15]) # montreal races
#list_index_sel = np.array([11, 16]) # Ottawa races
#list_index_sel = np.array([12]) # Harricana races


# apply color per trace
for tt in list_index_sel:
    one_run_trace  = [(x,y) for (x,y) in zip(list_run_df[tt]["latitude"].iloc[:].to_list(), 
                                             list_run_df[tt]["longitude"].iloc[:].to_list())]

    one_run_elevation = [z / maxElevation for z in list_run_df[tt]["elevation"].iloc[:].to_list()] 
    
    #folium.PolyLine(one_run_trace, tooltip="one_run", color="pink").add_to(westmount)
    colors = np.ones(len(one_run_elevation))
    folium.ColorLine(positions = one_run_trace, 
                             #tooltip = "one_run", 
                             colors = one_run_elevation,
                             colormap = ["pink","red"],
                             weight=1).add_to(mapSingleRace)
    locations.extend(one_run_trace)
# Display one gpd 
mapSingleRace.save("../tmp/"+mapName+".html")
mapSingleRace